### 遺伝的アルゴリズムとは
データを一定のルールに従って変化させていき、試行錯誤で最適な解を求める手法。

（巡回セールスマン問題、など）

### ソルバーによる最適化との違い
- ソルバー...解を**厳密**に求めようとする
- 遺伝的アルゴリズム...解を**探索的**に求める(メタヒューリスティクス)

### 例題

0か1を取る100個の数列がある。

数列の偶数番目の合計から、奇数番目の合計を引いた時の値が最大となる数列は何か？


In [ ]:
from deap import base
from deap import creator
from deap import tools
from deap import algorithms
import random
import numpy as np

#最小化？最大化？
creator.create("FitnessMax", base.Fitness, weights=(1.0,))

#個体の定義
creator.create("Individual", list, fitness=creator.FitnessMax)

toolbox = base.Toolbox()
#各個体の遺伝子の中身を決める関数(0 or 1)
toolbox.register("attr_bool", random.randint, 0, 1) 
#個体に含まれる遺伝子の数
toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_bool, n=100)

#集団の個体数を設定するための関数
toolbox.register("population", tools.initRepeat, list, toolbox.individual)
#次世代に子を残す親を選択する方法
toolbox.register("select", tools.selTournament, tournsize=5)
#交叉関数
toolbox.register("mate", tools.cxTwoPoint)
#突然変異関数（indpb=遺伝子が突然変異を起こす確率)
toolbox.register("mutate", tools.mutFlipBit, indpb=0.1)

#最適化させるのは何？
def eval_sample(individual):
    ans = sum(individual[1::2]) - sum(individual[::2])
    return ans,

toolbox.register("evaluate", eval_sample)

###アルゴリズムのパラメータ設定
random.seed(64) #乱数を固定
NGEN = 20 #何世代まで行うか
POP = 10 #集団の個体数
CXPB = 0.8 #交叉確率
MUTPB = 0.1 #個体が突然変異を起こす確率

#集団情報の設定
pop = toolbox.population(n=POP)

#集団内の個体それぞれの目的関数を計算
for individual in pop:
    individual.fitness.values = toolbox.evaluate(individual)
    
#良い結果の個体を抽出
hof = tools.ParetoFront()

#シンプルな手法を適用
algorithms.eaSimple(pop, toolbox, cxpb=CXPB, mutpb=MUTPB, ngen=NGEN, halloffame=hof)

#最終的な集団からベストな個体を選ぶ
best_ind = tools.selBest(pop, 1)[0]

#結果表示
print(best_ind)
print(best_ind.fitness.values)


In [ ]:
individual = [1,2,3,4,5,6]
individual[1::2]

[1, 0, 0, 1, 1]
(14.0,)

### 例題

300円で遠足に持っていくお菓子を選びたい。　

同じお菓子は2つ以上買わないと決めた時、もっとも満足度の高い組み合わせは何か？

|お菓子|満足度|値段|
|---|---|---|
|チョコレート|4|80円|
|ポテトチップス|5|120円|
|クッキー|6|140円|
|グミ|3|60円|
|バナナ|7|150円|

In [ ]:
from deap import base
from deap import creator
from deap import tools
from deap import algorithms
import random
import numpy as np

#最小化？最大化？
creator.create("FitnessMax", base.Fitness, weights=(1.0,))

#個体の定義
creator.create("Individual", list, fitness=creator.FitnessMax)

toolbox = base.Toolbox()
#各個体の遺伝子の中身を決める関数(0 or 1)
toolbox.register("attr_bool", random.randint, 0, 1) 
#個体に含まれる遺伝子の数
toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_bool, n=5)

#集団の個体数を設定するための関数
toolbox.register("population", tools.initRepeat, list, toolbox.individual)
#次世代に子を残す親を選択する方法
toolbox.register("select", tools.selTournament, tournsize=5)
#交叉関数
toolbox.register("mate", tools.cxTwoPoint)
#突然変異関数（indpb=遺伝子が突然変異を起こす確率)
toolbox.register("mutate", tools.mutFlipBit, indpb=0.1)

#最適化させるのは何？
def eval_sample(individual):
    ans = np.dot(individual,[4,5,6,3,7])
    return ans,

def feasible(individual):
    if np.dot(individual,[80,120,140,60,150]) <= 300:
        return True
    else:
        return False

toolbox.register("evaluate", eval_sample)
toolbox.decorate("evaluate", tools.DeltaPenalty(feasible,-1.0))

###アルゴリズムのパラメータ設定
random.seed(64) #乱数を固定
NGEN = 100 #何世代まで行うか
POP = 50 #集団の個体数
CXPB = 0.8 #交叉確率
MUTPB = 0.1 #個体が突然変異を起こす確率

#集団情報の設定
pop = toolbox.population(n=POP)

#集団内の個体それぞれの目的関数を計算
for individual in pop:
    individual.fitness.values = toolbox.evaluate(individual)
    
#良い結果の個体を抽出
hof = tools.ParetoFront()

#シンプルな手法を適用
algorithms.eaSimple(pop, toolbox, cxpb=CXPB, mutpb=MUTPB, ngen=NGEN, halloffame=hof)

#最終的な集団からベストな個体を選ぶ
best_ind = tools.selBest(pop, 1)[0]

#結果表示
print(best_ind)
print(best_ind.fitness.values)
